In [1]:
# importing packages

# Basic python packages
import pandas as pd
import numpy as np
import bertopic
import os
from os.path import join
#import datamapplot

# BERTopic related
from bertopic import BERTopic
from bertopic.representation import KeyBERTInspired
from umap import UMAP
from hdbscan import HDBSCAN
from sklearn.feature_extraction.text import CountVectorizer

# Transformers packages
from sentence_transformers import SentenceTransformer
import transformers
# handle parallelism for tokenizer
os.environ["TOKENIZERS_PARALLELISM"] = "false"

# SpaCy
import spacy
from spacy.lang.da import Danish

# viz packages
import matplotlib.pyplot as plt
import topicwizard
from topicwizard.compatibility import BERTopicWrapper
from topicwizard.figures import topic_map
import plotly.express as px
import plotly.graph_objects as go
from topicwizard.figures import *

In [2]:
output_dir= '/work/Ccp-MePSDA/output/plots'

In [3]:
# Loading data
bts_df = pd.read_csv('/work/Ccp-MePSDA/output/collected_data/bts_df.csv')
#mepsda_df.drop(columns='index', inplace=True)
bts_df['chunked'] = bts_df['chunked'].astype(str)
# select columns
bts_df = bts_df[['source', 'title', 'chunk_index', 'chunked']]

In [4]:
# Load from directory
# Defining embedding model
embedding_model = SentenceTransformer('intfloat/multilingual-e5-small')
topic_model = BERTopic.load("/work/Ccp-MePSDA/modelling/model/bts_bertopic", embedding_model=embedding_model)

# creating wrapper for topicwizard
wrapped_model = BERTopicWrapper(topic_model)

In [4]:
topic_model.get_topic_info()

Topic  Count                                               Name  \
0      -1    683           -1_tror når_vigtigt ja_gerne se_tror nej   
1       0     45   0_nej sjovt_ment første_mødt ja_kringeligt vildt   
2       1     37  1_føler ret_bare generelt_oplevelsen ret_tænke...   
3       2     36   2_tager tager_opvisninger_poul forstår_hæld prøv   
4       3     35       3_sagt gav_fået tænkt_øjne ja_prøvede hjælpe   
5       4     35  4_seriøst fortælle_siger tænkt_snakke nej_slåe...   
6       5     33  5_nej gerne_mærkeligt ja_tænker nej_bare mærke...   
7       6     32  6_optagelserne altså_10 afsnit_optaget altså_a...   
8       7     32  7_sjovt tror_hvilket altså_altså sjove_flotter...   
9       8     30  8_venlig gruppe_rigtig hyggeligt_synspunkter a...   
10      9     27  9_eksempel klippe_ja sidst_sagtens ske_små kli...   
11     10     26  10_kærester ja_ja kærester_ægte nogens_kæreste...   
12     11     26  11_måde altså_tænker mærkeligt_mener hjælpe_se...   
13     12     26  12_føles hverdagsagtigt_hverdagsagtigt_ja gene...   
14     13     25  13_spørger snackkuchen_snackkurven rigtig_rigt...   
15     14     25  14_bare sagde_reagere forstår_føler usagt_vids...   
16     15     24  15_hvadíveligt tænkte_lytte undskyld_gerne lyt...   
17     16     23  16_karakterer måde_måden snakker_forældre føle...   
18     17     23  17_billede taget_tror fedt_ja tager_ord kærlighed   
19     18     23    18_sagde frede_bare fået_begynde hej_ja prøvede   
20     19     23          19_sødt se_se sødt_se herunder_dansk godt   
21     20     23  20_anka sagde_gerne blevet_agtigt føler_godt s...   
22     21     21  21_tillykke tillykke_tak fortalte_kigget okay_...   
23     22     19  22_fortalte sagde_fortalte hinanden_sagde godt...   
24     23     19  23_desværre sine_føler fordomme_fortæller svær...   
25     24     19  24_forstår håber_forstår prøvet_føler normale_...   
26     25     18  25_filmet sagde_camilla oplevet_jonas sagde_få...   
27     26     18  26_altså følte_fucking behageligt_helt trætte_...   
28     27     18  27_læseprøven gik_bruge sagde_hedder læseprøve...   
29     28     18  28_altså hårdt_hårdt altså_forfærdeligt ja_hår...   
30     29     17  29_godt skuespiller_føler måde_hårdt egentlig_...   
31     30     16  30_dejligt føler_køn prøvet_måtte spændende_fe...   
32     31     16  31_tænkte gerne_søster ja_tage søster_fredag t...   
33     32     16  32_artig nej_swiper nej_ja photoshoppet_godt pænt   

                                       Representation  Representative_Docs  
0   [tror når, vigtigt ja, gerne se, tror nej, ja ...                  NaN  
1   [nej sjovt, ment første, mødt ja, kringeligt v...                  NaN  
2   [føler ret, bare generelt, oplevelsen ret, tæn...                  NaN  
3   [tager tager, opvisninger, poul forstår, hæld ...                  NaN  
4   [sagt gav, fået tænkt, øjne ja, prøvede hjælpe...                  NaN  
5   [seriøst fortælle, siger tænkt, snakke nej, sl...                  NaN  
6   [nej gerne, mærkeligt ja, tænker nej, bare mær...                  NaN  
7   [optagelserne altså, 10 afsnit, optaget altså,...                  NaN  
8   [sjovt tror, hvilket altså, altså sjove, flott...                  NaN  
9   [venlig gruppe, rigtig hyggeligt, synspunkter ...                  NaN  
10  [eksempel klippe, ja sidst, sagtens ske, små k...                  NaN  
11  [kærester ja, ja kærester, ægte nogens, kærest...                  NaN  
12  [måde altså, tænker mærkeligt, mener hjælpe, s...                  NaN  
13  [føles hverdagsagtigt, hverdagsagtigt, ja gene...                  NaN  
14  [spørger snackkuchen, snackkurven rigtig, rigt...                  NaN  
15  [bare sagde, reagere forstår, føler usagt, vid...                  NaN  
16  [hvadíveligt tænkte, lytte undskyld, gerne lyt...                  NaN  
17  [karakterer måde, måden snakker, forældre føle...                  NaN  
18  [billede taget, tror fedt, ja tager, ord kærli...  

In [ ]:
# Further reduce topics
topic_model.reduce_topics(bts_df['chunked'], nr_topics=21)

# Saving once again after merging
topic_model.save("/work/Ccp-MePSDA/modelling/model/bts_bertopic", serialization="safetensors", save_ctfidf=True, save_embedding_model=embedding_model)

2024-12-17 09:46:51,980 - BERTopic - Topic reduction - Reducing number of topics
2024-12-17 09:46:52,076 - BERTopic - Topic reduction - Reduced number of topics from 34 to 21


In [20]:
hierarchical_topics = topic_model.hierarchical_topics(bts_df['chunked'])

topic_hierarchy = topic_model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

topic_hierarchy.update_layout(
    title="Hierarchical Clusering BTS-material",
    title_font_size=26
)
topic_hierarchy.show()
topic_hierarchy.write_html(join(output_dir, 'bts_topic_hiearchy.html'))

100%|██████████| 19/19 [00:00<00:00, 327.49it/s]


In [21]:
# Loading embeddings
embeddings = np.load('/work/Ccp-MePSDA/modelling/embeddings/bts_embeddings.npy')
# Run the visualization with the original embeddings
#topic_model.visualize_hierarchical_documents(mepsda_df['chunked'], hierarchical_topics, embeddings=embeddings)

# Reduce dimensionality of embeddings, this step is optional but much faster to perform iteratively:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
hierarchy_doc_topic = topic_model.visualize_hierarchical_documents(bts_df['chunked'], hierarchical_topics, reduced_embeddings=reduced_embeddings)
hierarchy_doc_topic.update_layout(
    title='hierarchical doc mapping for BTS-material',
    title_font_size=26
)
hierarchy_doc_topic.write_html('/work/Ccp-MePSDA/output/plots/hierarchy_doc_bts.html')

In [22]:
term_rank = topic_model.visualize_term_rank()

term_rank.write_html('/work/Ccp-MePSDA/output/plots/bts_term_rank.html')

Topic Wizard plots

In [5]:
# Produce a TopicData object for persistance or figures.
topic_data = wrapped_model.prepare_topic_data(bts_df['chunked'])

In [7]:
wizard_bar = topic_barcharts(topic_data, top_n=8)
# Add a title
wizard_bar.update_layout(
    title="Top Terms Across Topics for BTS-material",
    title_font_size=26
)

# Change chart size
wizard_bar.update_layout(
    height=1500,
    width=2000
)

# Adjust bar width
wizard_bar.update_traces(
   width=1
)

wizard_bar.show()
wizard_bar.write_html('/work/Ccp-MePSDA/output/plots/bts_wizard_bar.html')

In [8]:
word_map = word_map(topic_data)  # Generate the figure
word_map.show()  # Display the plot

word_map.write_html('/work/Ccp-MePSDA/output/plots/bts_word_map.html')

In [9]:
document_map = document_map(topic_data)
document_map.show()


document_map.write_html('/work/Ccp-MePSDA/output/plots/bts_document_map.html')

In [29]:
keyword_sim = pd.read_csv('/work/Ccp-MePSDA/output/keyword_search/mepsda_chunk_keywordsimilarity.csv')

In [13]:
fig = go.Figure()

# Add the histogram for theme 1
fig.add_trace(go.Histogram(
    x=keyword_sim['theme1_similarity'],
    opacity=0.6,
    name='Theme 1'
))

# Add the histogram for theme 2
fig.add_trace(go.Histogram(
    x=keyword_sim['theme2_similarity'],
    opacity=0.6,
    name='Theme 2'
))

# Add the histogram for theme 3
fig.add_trace(go.Histogram(
    x=keyword_sim['theme3_similarity'],
    opacity=0.6,
    name='Theme 3'
))

# Update the layout
fig.update_layout(
    title='Distribution of BTS Similarity Scores by Keyword Theme',
    title_font_size=22,
    xaxis_title='Cosine Similarity',
    yaxis_title='Frequency',
    legend_title_text='Theme'
)

# Show the plot
fig.show()
fig.write_html('/work/Ccp-MePSDA/output/plots/bts_histogram.html')